# 03 - Interactive Viz

## Deadline

Wednesday November 8th, 2017 at 11:59PM

## Important Notes

- Make sure you push on GitHub your Notebook with all the cells already evaluated
- Note that maps do not render in a standard Github environment : you should export them to HTML and link them in your notebook.
- Remember that `.csv` is not the only data format. Though they might require additional processing, some formats provide better encoding support.
- Don't forget to add a textual description of your thought process, the assumptions you made, and the solution you plan to implement!
- Please write all your comments in English, and use meaningful variable names in your code

## Background

In this homework we will be exploring interactive visualization, which is a key ingredient of many successful data visualizations (especially when it comes to infographics).

Unemployment rates are major economic metrics and a matter of concern for governments around the world. Though its definition may seem straightforward at first glance (usually defined as the number of unemployed people divided by the active population), it can be tricky to define consistently. For example, one must define what exactly unemployed means : looking for a job ? Having declared their unemployment ? Currently without a job ? Should students or recent graduates be included ? We could also wonder what the active population is : everyone in an age category (e.g. `16-64`) ? Anyone interested by finding a job ? Though these questions may seem subtle, they can have a large impact on the interpretation of the results : `3%` unemployment doesn't mean much if we don't know who is included in this percentage. 

In this homework you will be dealing with two different datasets from the statistics offices of the European commission ([eurostat](http://ec.europa.eu/eurostat/data/database)) and the Swiss Confederation ([amstat](https://www.amstat.ch)). They provide a variety of datasets with plenty of information on many different statistics and demographics at their respective scales. Unfortunately, as is often the case is data analysis, these websites are not always straightforward to navigate. They may include a lot of obscure categories, not always be translated into your native language, have strange link structures, â€¦ Navigating this complexity is part of a data scientists' job : you will have to use a few tricks to get the right data for this homework.

For the visualization part, install [Folium](https://github.com/python-visualization/folium) (*HINT*: it is not available in your standard Anaconda environment, therefore search on the Web how to install it easily!). Folium's `README` comes with very clear examples, and links to their own iPython Notebooks -- make good use of this information. For your own convenience, in this same directory you can already find two `.topojson` files, containing the geo-coordinates of 

- European countries (*liberal definition of EU*) (`topojson/europe.topojson.json`, [source](https://github.com/leakyMirror/map-of-europe))
- Swiss cantons (`topojson/ch-cantons.topojson.json`) 

These will be used as an overlay on the Folium maps.

## Assignment

1. Go to the [eurostat](http://ec.europa.eu/eurostat/data/database) website and try to find a dataset that includes the european unemployment rates at a recent date.

   Use this data to build a [Choropleth map](https://en.wikipedia.org/wiki/Choropleth_map) which shows the unemployment rate in Europe at a country level. Think about [the colors you use](https://carto.com/academy/courses/intermediate-design/choose-colors-1/), how you decided to [split the intervals into data classes](http://gisgeography.com/choropleth-maps-data-classification/) or which interactions you could add in order to make the visualization intuitive and expressive. Compare Switzerland's unemployment rate to that of the rest of Europe.

2. Go to the [amstat](https://www.amstat.ch) website to find a dataset that includes the unemployment rates in Switzerland at a recent date.

   > *HINT* Go to the `details` tab to find the raw data you need. If you do not speak French, German or Italian, think of using free translation services to navigate your way through. 

   Use this data to build another Choropleth map, this time showing the unemployment rate at the level of swiss cantons. Again, try to make the map as expressive as possible, and comment on the trends you observe.

   The Swiss Confederation defines the rates you have just plotted as the number of people looking for a job divided by the size of the active population (scaled by 100). This is surely a valid choice, but as we discussed one could argue for a different categorization.

   Copy the map you have just created, but this time don't count in your statistics people who already have a job and are looking for a new one. How do your observations change ? You can repeat this with different choices of categories to see how selecting different metrics can lead to different interpretations of the same data.

3. Use the [amstat](https://www.amstat.ch) website again to find a dataset that includes the unemployment rates in Switzerland at recent date, this time making a distinction between *Swiss* and *foreign* workers.

   The Economic Secretary (SECO) releases [a monthly report](https://www.seco.admin.ch/seco/fr/home/Arbeit/Arbeitslosenversicherung/arbeitslosenzahlen.html) on the state of the employment market. In the latest report (September 2017), it is noted that there is a discrepancy between the unemployment rates for *foreign* (`5.1%`) and *Swiss* (`2.2%`) workers. 

   Show the difference in unemployment rates between the two categories in each canton on a Choropleth map (*hint* The easy way is to show two separate maps, but can you think of something better ?). Where are the differences most visible ? Why do you think that is ?

   Now let's refine the analysis by adding the differences between age groups. As you may have guessed it is nearly impossible to plot so many variables on a map. Make a bar plot, which is a better suited visualization tool for this type of multivariate data.

4. *BONUS*: using the map you have just built, and the geographical information contained in it, could you give a *rough estimate* of the difference in unemployment rates between the areas divided by the [RÃ¶stigraben](https://en.wikipedia.org/wiki/R%C3%B6stigraben)?

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib as mpl
import seaborn as sns
%matplotlib inline

[tsdsc330] - Long-term unemployment rate, by sex

Long-term unemployed (12 months and more) comprise persons aged at least 15, who are not living in collective households, who will be without work during the next two weeks, who would be available to start work within the next two weeks and who are seeking work (have actively sought employment at some time during the previous four weeks or are not seeking a job because they have already found a job to start later). The total active population (labour force) is the total number of the employed and unemployed population. The duration of unemployment is defined as the duration of a search for a job or as the period of time since the last job was held (if this period is shorter than the duration of the search for a job).

LEGEND
* **:** are non available data
* **b** break in the time serie
* **e** for estimated
* **u** low relialability
* **PC** for percentage
* **PPCH** for percentage point change t/(t-3)

where:      
_A percentage point or percent point (pp) is the unit for the arithmetic difference of two percentages. For example, moving up from 40% to 44% is a 4 percentage point increase, but is an actual 10 percent increase in what is being measured._



DATA_FOLDER = 'data/'
eurodf = pd.read_csv(DATA_FOLDER + 'tsdsc330.tsv' , sep='\t|,|[|]', engine='python')
eurodf.head(2)

eurodf.replace(to_replace=':', value='nan',inplace=True, regex=True)
eurodf.head(2)

Since the columns 'indic_em', 'age', 'unit' list only one value, they don't provide us any information and to be as clear as possible we drop them

eurodf.drop(['indic_em','age','unit'],inplace=True, axis=1)
eurodf.columns.values[1] = 'country code'

codes = pd.DataFrame([eurodf[eurodf['sex']=='T']['country code'].reset_index(drop=True),
                     eurodf[eurodf['sex']=='F']['country code'].reset_index(drop=True),
                     eurodf[eurodf['sex']=='M']['country code'].reset_index(drop=True)])
codes

We are interested in noticing how many data are considered of low reliability, and so carachterized by a 'u'. 

eurodf.replace(['b','e'],['',''],regex=True,inplace=True)
count = 0
for col in eurodf.columns[2:]:
    for cell in eurodf[col]:
        if 'u' in cell:
            count=count+1
print(count)
eurodf.head()

Now we can get rid of all the non-numeric flag that accompany each number:

years = list(eurodf.columns[2:].astype(int))

eurodf.replace('u','',regex=True,inplace=True)
eurodf[eurodf.columns[2:]]=eurodf[eurodf.columns[2:]].astype(float)

fig, axes =  plt.subplots(12,3, figsize=[20,40])
totaldf = eurodf[eurodf["sex"]=='T'].reset_index(drop=True)
maledf = eurodf[eurodf["sex"]=='M'].reset_index(drop=True)
femaledf = eurodf[eurodf["sex"]=='F'].reset_index(drop=True)

for i,ax in enumerate(axes.reshape(-1)):
    mpl.style.use('default')
    ax.plot_date(years, totaldf.loc[i][2:], 'C1', label="T")
    ax.plot_date(years, maledf.loc[i][2:], 'C2', label="M")
    ax.plot_date(years, femaledf.loc[i][2:], 'C3', label="F")
    ax.set_title(totaldf.loc[i][1])
    ax.set_ylim(0,35)
    ax.set_xlim(1996,2016)
    ax.set_facecolor('white')
    #ax.set_xticks(np.arange(1996,2016,4))
    ax.legend()
    ax.grid()
fig.tight_layout()
plt.show()

It could be interesting to see which nations have a higher difference in the unemplyment rate for male and women:

diffdf = maledf[maledf.columns[2:]].subtract(femaledf[femaledf.columns[2:]],axis='columns')

diffdf=diffdf.transpose()
diffdf.columns=maledf['country code']

fig2, ax2 =  plt.subplots(2, figsize=(15,15))
sns.boxplot(data=diffdf[diffdf.columns[:18]], palette="Set3", ax = ax2[0])
sns.boxplot(data=diffdf[diffdf.columns[18:]], palette="Set3", ax = ax2[1])
ax2[0].grid()
ax2[1].grid()

# STOP HERE!!!


In [14]:
chdf = pd.read_excel(DATA_FOLDER + 'ch.xlsx',header=[0,1])

chdf.head(10)

FileNotFoundError: [Errno 2] No such file or directory: 'data/ch.xlsx'

In [ ]:
tasso = chdf[month,'Tasso di disoccupazione']*
        (chdf[month,'Disoccupati registrati']-chdf[month,'Disoccupati Persone in cerca d\'impiego]-